In [1]:
import torch
from torch.utils.data import Dataset, DataLoader
import os, os.path 
import numpy 
import pickle
from glob import glob
from tqdm.notebook import tqdm, trange

"""Change to the data folder"""
new_path = "./new_train/new_train"

cuda_status = torch.cuda.is_available()
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# number of sequences in each dataset
# train:205942  val:3200 test: 36272 
# sequences sampled at 10HZ rate

### Create a dataset class 

In [2]:
class ArgoverseDataset(Dataset):
    """Dataset class for Argoverse"""
    def __init__(self, data_path: str, transform=None):
        super(ArgoverseDataset, self).__init__()
        self.data_path = data_path
        self.transform = transform

        self.pkl_list = glob(os.path.join(self.data_path, '*'))
        self.pkl_list.sort()
        
    def __len__(self):
        return len(self.pkl_list)

    def __getitem__(self, idx):

        pkl_path = self.pkl_list[idx]
        with open(pkl_path, 'rb') as f:
            data = pickle.load(f)
        
        if self.transform:
            data = self.transform(data)

        return data


# intialize a dataset
val_dataset  = ArgoverseDataset(data_path=new_path)

### Create a loader to enable batch processing

In [ ]:
batch_sz = 512

def my_collate(batch):
    """ collate lists of samples into batches, create [ batch_sz x agent_sz x seq_len x feature] """
    inp = [numpy.dstack([scene['p_in'], scene['v_in']]) for scene in batch]
    out = [numpy.dstack([scene['p_out'], scene['v_out']]) for scene in batch]
    scene_ids = [scene['scene_idx'] for scene in batch]
    track_ids = [scene['track_id'] for scene in batch]
    agent_ids = [scene['agent_id'] for scene in batch]
    car_mask = [scene['car_mask'] for scene in batch]
    inp = torch.LongTensor(inp)
    out = torch.LongTensor(out)
    scene_ids = torch.LongTensor(scene_ids)
    car_mask = torch.LongTensor(car_mask)
    return [inp, out, scene_ids, track_ids, agent_ids, car_mask]

def test_collate(batch):
    """ collate lists of samples into batches, create [ batch_sz x agent_sz x seq_len x feature] """
    inp = [numpy.dstack([scene['p_in'], scene['v_in']]) for scene in batch]
    scene_ids = [scene['scene_idx'] for scene in batch]
    track_ids = [scene['track_id'] for scene in batch]
    agent_ids = [scene['agent_id'] for scene in batch]
    inp = torch.LongTensor(inp)
    scene_ids = torch.LongTensor(scene_ids)
    return [inp, scene_ids, track_ids, agent_ids]

temp_loader = DataLoader(val_dataset,batch_size=205942, shuffle = False, collate_fn=my_collate, num_workers=0, drop_last=True)
data = next(iter(temp_loader))
inp, out, scene_ids, track_ids, agent_ids, car_mask = data
print(inp.mean())
print(inp.std())
print(out.mean())
print(out.std())

val_loader = DataLoader(val_dataset,batch_size=batch_sz, shuffle = False, collate_fn=my_collate, num_workers=0, drop_last=True)

In [11]:
class RNNEncoderDecoder(torch.nn.Module):
    def __init__(self):
        super().__init__()
        self.encoder = torch.nn.RNN(240, hidden_size=512, batch_first=True, nonlinearity='relu')
        self.decoder = torch.nn.RNN(240, hidden_size=512, batch_first=True, nonlinearity='relu')
        
        self.align1 = torch.nn.Linear(10240, 19)
        #self.attn = Attention(512,512)
        
        self.linear = torch.nn.Linear(512, 240)

    def forward(self, x, y, teach = False, teaching_ratio = 0.5):
        # batch_szx60x19x4
        x = x.permute(0,2,1,3)
        x = torch.flatten(x, start_dim=2)
        # batch_szx19x240
        output, hidden = self.encoder(x)
        
        outputs = torch.zeros(30,batch_sz,60,4).to(device).cuda()
        dec_out, dec_hidden = self.decoder(torch.full((batch_sz,1,240), -1).to(device).cuda(), hidden)
        # dec_out: batch_szx1x512
        dec_out = dec_out.permute(1,0,2).squeeze(0)
        # batch_szx512
        dec_out = self.linear(dec_out)
        # batch_sz x 240
        outputs[0] = torch.reshape(dec_out, torch.Size([batch_sz, 60, 4]))
        
        if teach:
            next_in = torch.flatten(y[:,:,0,:].squeeze(2), start_dim=1).unsqueeze(1)
            # batch_szx240
        else:
            next_in = dec_out.unsqueeze(1)
        
        # output: batch_szx19x512
        # h_n: 1xbatch_szx512
        prevState = hidden.permute(1,0,2)
        inputStates = output
        
        for i in range(1,30):
            alignment = self.align1(torch.flatten(torch.cat((inputStates, prevState), 1), start_dim=1))
            #batch_szx19
            
            attention = torch.nn.functional.softmax(alignment, dim=1)
            attention = attention.unsqueeze(1)
            #batch_szx1x19
            
            new_hidden = torch.bmm(attention, inputStates)
            new_hidden = new_hidden.permute(1,0,2)
            #1xbatch_szx512
             
            dec_out, dec_hidden = self.decoder(next_in, new_hidden)
            # dec_out: batch_szx1x512
            dec_out = dec_out.permute(1,0,2).squeeze(0)
            # batch_szx512
            dec_out = self.linear(dec_out)
            # batch_sz x 240
            
            teaching = random.random() < teaching_ratio
            
            if teach and teaching:
                next_in = torch.flatten(y[:,:,i-1,:].squeeze(2), start_dim=1).unsqueeze(1)
            else:
                next_in = dec_out.unsqueeze(1)
                
            outputs[i] = torch.reshape(dec_out, torch.Size([batch_sz, 60, 4]))
            
            prevState = dec_hidden.permute(1,0,2)
        
        return outputs.permute(1,2,0,3)

model = RNNEncoderDecoder()
model.to(device)
if cuda_status:
    model = model.cuda()

### Visualize the batch of sequences

In [12]:
import matplotlib.pyplot as plt
import random
from tqdm.notebook import tqdm

agent_id = 0
epoch = 3
        
# Use the nn package to define our loss function
loss_fn=torch.nn.MSELoss()

# Use the optim package to define an Optimizer

learning_rate =1e-3
#learning_rate =0.01
#optimizer = torch.optim.RMSprop(model.parameters(), lr=learning_rate)
optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate)
iterator = tqdm(val_loader)

for i in trange(epoch):
    
    for i_batch, sample_batch in enumerate(iterator):
        inp, out, scene_ids, track_ids, agent_ids, car_mask = sample_batch
        """TODO:
          Deep learning model
          training routine
        """
        
        x = inp.float()
        y = out.float()

        if cuda_status:
            x.to(device)
            y.to(device)
            x = x.cuda()
            y = y.cuda()

        y_pred = None
        # Forward pass: predict y by passing x to the model.    
        y_pred = model(x, y, False)
        #y_pred = torch.reshape(y_pred, torch.Size([batch_sz, 60, 30, 4]))

        # Compute the loss.
        loss = loss_fn(y_pred, y)

        # Before backward pass, zero outgradients to clear buffers  
        optimizer.zero_grad()

        # Backward pass: compute gradient w.r.t modelparameters
        loss.backward()

        # makes an gradient descent step to update its parameters
        optimizer.step()
        
        print(torch.sqrt(loss).item(), end='\r')


{'city': 'PIT', 'lane': array([[3278.8716, 1968.7596,    0.    ],
       [3282.6606, 1972.2533,    0.    ],
       [3286.4429, 1975.7545,    0.    ],
       [3290.2249, 1979.2559,    0.    ],
       [3294.007 , 1982.7572,    0.    ],
       [3297.789 , 1986.2584,    0.    ],
       [3301.5713, 1989.7598,    0.    ],
       [3305.3533, 1993.2611,    0.    ],
       [3309.1355, 1996.7623,    0.    ],
       [3269.4802, 1967.0625,    0.    ],
       [3267.2764, 1965.0217,    0.    ],
       [3265.0664, 1962.9877,    0.    ],
       [3262.8562, 1960.9536,    0.    ],
       [3260.646 , 1958.9197,    0.    ],
       [3258.436 , 1956.8856,    0.    ],
       [3256.2258, 1954.8517,    0.    ],
       [3254.0132, 1952.8207,    0.    ],
       [3251.7898, 1950.8013,    0.    ],
       [3235.7622, 1935.9915,    0.    ],
       [3231.5237, 1932.1249,    0.    ],
       [3227.2852, 1928.2582,    0.    ],
       [3223.0923, 1924.343 ,    0.    ],
       [3218.9045, 1920.4214,    0.    ],
       [32

{'city': 'PIT', 'lane': array([[3855.859 , 2232.4053,    0.    ],
       [3859.7212, 2233.9846,    0.    ],
       [3863.5168, 2235.7087,    0.    ],
       [3867.3005, 2237.4583,    0.    ],
       [3871.1543, 2239.0593,    0.    ],
       [3875.049 , 2240.549 ,    0.    ],
       [3878.9993, 2241.8894,    0.    ],
       [3883.0676, 2242.8047,    0.    ],
       [3887.1987, 2243.3994,    0.    ],
       [3929.784 , 2252.613 ,    0.    ],
       [3927.6108, 2252.3289,    0.    ],
       [3925.4377, 2252.0447,    0.    ],
       [3923.2646, 2251.7605,    0.    ],
       [3921.0916, 2251.4763,    0.    ],
       [3918.9185, 2251.1921,    0.    ],
       [3916.7456, 2250.908 ,    0.    ],
       [3914.5725, 2250.6238,    0.    ],
       [3912.3994, 2250.3396,    0.    ],
       [3869.8562, 2227.841 ,    0.    ],
       [3868.2893, 2231.8813,    0.    ],
       [3866.7227, 2235.9214,    0.    ],
       [3865.1636, 2239.9646,    0.    ],
       [3863.648 , 2244.0225,    0.    ],
       [38

{'city': 'MIA', 'lane': array([[ 779.42664, 2408.2197 ,    0.     ],
       [ 778.8532 , 2408.2004 ,    0.     ],
       [ 778.27985, 2408.181  ,    0.     ],
       [ 777.7064 , 2408.1616 ,    0.     ],
       [ 777.13306, 2408.142  ,    0.     ],
       [ 776.5597 , 2408.1228 ,    0.     ],
       [ 775.98627, 2408.1033 ,    0.     ],
       [ 775.4129 , 2408.0837 ,    0.     ],
       [ 774.8395 , 2408.0645 ,    0.     ],
       [ 767.7139 , 2404.6855 ,    0.     ],
       [ 768.617  , 2404.7122 ,    0.     ],
       [ 769.52   , 2404.7385 ,    0.     ],
       [ 770.42303, 2404.765  ,    0.     ],
       [ 771.32605, 2404.7913 ,    0.     ],
       [ 772.22906, 2404.8176 ,    0.     ],
       [ 773.1321 , 2404.844  ,    0.     ],
       [ 774.03516, 2404.8704 ,    0.     ],
       [ 774.9382 , 2404.8967 ,    0.     ],
       [ 773.93054, 2408.0374 ,    0.     ],
       [ 773.02155, 2408.0103 ,    0.     ],
       [ 772.1126 , 2407.9832 ,    0.     ],
       [ 771.2036 , 2407.956  ,

{'city': 'PIT', 'lane': array([[2321.7842 ,  840.37213,    0.     ],
       [2323.066  ,  841.8145 ,    0.     ],
       [2323.9546 ,  843.44226,    0.     ],
       [2324.2334 ,  845.2709 ,    0.     ],
       [2323.8342 ,  847.1187 ,    0.     ],
       [2322.8538 ,  848.7902 ,    0.     ],
       [2321.6895 ,  850.3564 ,    0.     ],
       [2320.4426 ,  851.8506 ,    0.     ],
       [2319.0408 ,  853.20483,    0.     ],
       [2309.0488 ,  863.90686,    0.     ],
       [2308.0974 ,  864.9077 ,    0.     ],
       [2307.1462 ,  865.90857,    0.     ],
       [2306.197  ,  866.91156,    0.     ],
       [2305.2595 ,  867.92554,    0.     ],
       [2304.3162 ,  868.9339 ,    0.     ],
       [2303.3677 ,  869.9375 ,    0.     ],
       [2302.4192 ,  870.9411 ,    0.     ],
       [2301.4705 ,  871.94464,    0.     ],
       [2330.518  ,  854.5796 ,    0.     ],
       [2329.2285 ,  853.4998 ,    0.     ],
       [2327.9265 ,  852.43634,    0.     ],
       [2326.5186 ,  851.5277 ,

{'city': 'PIT', 'lane': array([[3166.9822, 1673.7092,    0.    ],
       [3165.898 , 1672.7544,    0.    ],
       [3164.814 , 1671.7996,    0.    ],
       [3163.7297, 1670.8448,    0.    ],
       [3162.6455, 1669.89  ,    0.    ],
       [3161.5613, 1668.9353,    0.    ],
       [3160.4773, 1667.9805,    0.    ],
       [3159.393 , 1667.0258,    0.    ],
       [3158.3088, 1666.0709,    0.    ],
       [3213.692 , 1641.4071,    0.    ],
       [3213.4585, 1641.6428,    0.    ],
       [3213.225 , 1641.8784,    0.    ],
       [3212.9868, 1642.1095,    0.    ],
       [3212.7485, 1642.3406,    0.    ],
       [3212.5105, 1642.5715,    0.    ],
       [3212.2722, 1642.8026,    0.    ],
       [3212.0342, 1643.0337,    0.    ],
       [3211.796 , 1643.2646,    0.    ],
       [3209.9124, 1645.1428,    0.    ],
       [3208.0288, 1647.021 ,    0.    ],
       [3206.1453, 1648.8992,    0.    ],
       [3204.2617, 1650.7773,    0.    ],
       [3202.3782, 1652.6554,    0.    ],
       [32

...

{'city': 'MIA', 'lane': array([[ 110.606766, 3265.9146  ,    0.      ],
       [ 109.86044 , 3266.2178  ,    0.      ],
       [ 109.1218  , 3266.5544  ,    0.      ],
       ...,
       [ 126.76297 , 3327.2346  ,    0.      ],
       [ 126.76604 , 3328.6174  ,    0.      ],
       [ 126.769104, 3330.      ,    0.      ]], dtype=float32), 'lane_norm': array([[-0.81068623,  0.00518932,  0.        ],
       [-0.7463248 ,  0.30334026,  0.        ],
       [-0.73863584,  0.33658883,  0.        ],
       ...,
       [ 0.0030659 ,  1.3826602 ,  0.        ],
       [ 0.0030659 ,  1.3826602 ,  0.        ],
       [ 0.0030659 ,  1.3826602 ,  0.        ]], dtype=float32), 'scene_idx': 100246, 'agent_id': '00000000-0000-0000-0000-000000046296', 'car_mask': array([[1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.

{'city': 'MIA', 'lane': array([[ 106.74009, 2331.1863 ,    0.     ],
       [ 105.05172, 2331.1187 ,    0.     ],
       [ 103.36335, 2331.0508 ,    0.     ],
       ...,
       [ 154.0243 , 2325.284  ,    0.     ],
       [ 154.014  , 2322.5234 ,    0.     ],
       [ 154.00371, 2319.7627 ,    0.     ]], dtype=float32), 'lane_norm': array([[-1.6883711 , -0.0678477 ,  0.        ],
       [-1.6883711 , -0.0678477 ,  0.        ],
       [-1.6883711 , -0.0678477 ,  0.        ],
       ...,
       [-0.01029973, -2.7605793 ,  0.        ],
       [-0.01029973, -2.7605793 ,  0.        ],
       [-0.01029973, -2.7605793 ,  0.        ]], dtype=float32), 'scene_idx': 100257, 'agent_id': '00000000-0000-0000-0000-000000028592', 'car_mask': array([[1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
  

{'city': 'MIA', 'lane': array([[ 554.06866, 2350.8757 ,    0.     ],
       [ 555.2835 , 2350.7217 ,    0.     ],
       [ 556.4623 , 2350.4028 ,    0.     ],
       ...,
       [ 553.5297 , 2397.1045 ,    0.     ],
       [ 553.8585 , 2397.1177 ,    0.     ],
       [ 554.1873 , 2397.1216 ,    0.     ]], dtype=float32), 'lane_norm': array([[ 1.2221984 , -0.12197297,  0.        ],
       [ 1.2148497 , -0.1538906 ,  0.        ],
       [ 1.1788079 , -0.31897703,  0.        ],
       ...,
       [ 0.328852  ,  0.01710322,  0.        ],
       [ 0.3288244 ,  0.01318312,  0.        ],
       [ 0.32875937,  0.00393784,  0.        ]], dtype=float32), 'scene_idx': 100271, 'agent_id': '00000000-0000-0000-0000-000000096067', 'car_mask': array([[1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
       [0.],
  

{'city': 'MIA', 'lane': array([[ 573.872  , 1888.8588 ,    0.     ],
       [ 573.9139 , 1887.7175 ,    0.     ],
       [ 573.95575, 1886.5762 ,    0.     ],
       [ 573.9976 , 1885.4349 ,    0.     ],
       [ 574.0395 , 1884.2937 ,    0.     ],
       [ 574.0814 , 1883.1525 ,    0.     ],
       [ 574.1233 , 1882.0112 ,    0.     ],
       [ 574.16516, 1880.87   ,    0.     ],
       [ 574.20703, 1879.7286 ,    0.     ],
       [ 562.03516, 1910.2266 ,    0.     ],
       [ 563.7824 , 1910.2301 ,    0.     ],
       [ 565.51733, 1910.0596 ,    0.     ],
       [ 567.079  , 1909.314  ,    0.     ],
       [ 568.31726, 1908.0927 ,    0.     ],
       [ 569.24866, 1906.6204 ,    0.     ],
       [ 569.8999 , 1905.004  ,    0.     ],
       [ 570.2895 , 1903.3058 ,    0.     ],
       [ 570.42786, 1901.5675 ,    0.     ],
       [ 577.0103 , 1891.283  ,    0.     ],
       [ 576.96655, 1892.5659 ,    0.     ],
       [ 576.9228 , 1893.8488 ,    0.     ],
       [ 576.879  , 1895.1317 ,

KeyboardInterrupt: 

In [10]:
torch.save(model, './models/3epoch-RNN-Encoder-Decoder-Attention-512-batch-no-teach.pt')

/opt/conda/lib/python3.7/site-packages/torch/serialization.py:256: UserWarning: Couldn't retrieve source code for container of type RNNEncoderDecoder. It won't be checked for correctness upon loading.
  "type " + obj.__name__ + ". It won't be checked "


In [ ]:
model = torch.load('./models/3epoch-RNN-Encoder-Decoder-Attention.pt')
model.eval()
model.to(device)
if cuda_status:
    model = model.cuda()

In [ ]:
import pandas as pd

# Submission output
writeCSV = True
val_path = "./new_val_in/new_val_in"

if writeCSV:
    
    dataset = ArgoverseDataset(data_path=val_path)
    test_loader = DataLoader(dataset,batch_size=64, shuffle = False, collate_fn=test_collate, num_workers=0)
    
    data = []
    
    with torch.no_grad():
        for i_batch, sample_batch in enumerate(tqdm(test_loader)):
            inp, scene_ids, track_ids, agent_ids = sample_batch

            if cuda_status:
                model = model.cuda()
                x = inp.float().cuda()
            else:
                x = inp.float()

            y_pred = None

            # Forward pass: predict y by passing x to the model.    
            y_pred = model(x, None, False)
            y_pred = torch.reshape(y_pred, torch.Size([batch_sz, 60, 30, 4]))
            
            for i in range(batch_sz):
                row = []
                row.append(scene_ids[i].item())
                curr = y_pred[i]
                
                agent_id = agent_ids[i]
                
                for j in range(30):
                    vehicle_index = 0
                    found = False
                    while not found:
                        if track_ids[i][vehicle_index][j][0] == agent_id:
                            found = True
                        else:
                            vehicle_index += 1

                    row.append(str(curr[vehicle_index][j][0].item()))
                    row.append(str(curr[vehicle_index][j][1].item()))
                    
                data.append(row)

    df = pd.DataFrame(data, columns = ['ID','v1','v2','v3','v4','v5','v6','v7','v8','v9','v10','v11','v12','v13','v14','v15','v16','v17','v18','v19','v20','v21','v22','v23','v24','v25','v26','v27','v28','v29','v30','v31','v32','v33','v34','v35','v36','v37','v38','v39','v40','v41','v42','v43','v44','v45','v46','v47','v48','v49','v50','v51','v52','v53','v54','v55','v56','v57','v58','v59','v60'])
    print(df)
    df.to_csv('submission.csv', index=False)
                
                
                